In [1]:
import healthForecaster as hF
import pandas as pd
import numpy as np
from pivottablejs import pivot_ui
from bqplot import pyplot as plt
from bqplot import axes
from sklearn import utils, model_selection, metrics, linear_model, neighbors, ensemble

## Preprocess raw data:

In [44]:
# Converts all the relevant SAS files to CSVs:
# NOTE: This takes a while! This only needs to be run once. 
if False: 
    preprocessRawChinaHealthStudyData()

## Aggregate relevant data for ML:

In [51]:
data = hF.createDataTable()
data

Adding demographic info
Adding gender.csv
Adding surveys_pub_12_2009only.csv
Adding hlth_12_2009only.csv
One-hot-encoding medical conditions...
Adding lifestyle features...
Adding c12diet_2009only.csv
Adding nutr2_00_2009only.csv
Adding reponse variables...
Adding biomarker_09_2009only.csv


idind   age  sex  urban  ENT  OBGYN  Old_age_midLife_syndrome  \
0     211101003002  58.0    0      1  0.0    0.0                       0.0   
1     211101010001  69.0    0      1  0.0    0.0                       0.0   
2     211101012001  61.0    1      1  0.0    0.0                       0.0   
3     211101012002  56.0    0      1  0.0    0.0                       0.0   
4     211101013002  66.0    0      1  0.0    0.0                       0.0   
...            ...   ...  ...    ...  ...    ...                       ...   
9543  522404121001  38.0    1      0  0.0    0.0                       0.0   
9544  522404121002  36.0    0      0  0.0    0.0                       0.0   
9545  522404121004  10.0    1      0  0.0    0.0                       0.0   
9546  522404122001  34.0    1      0  0.0    0.0                       0.0   
9547  522404122003  13.0    1      0  0.0    0.0                       0.0   

      alcohol_poisoning  dermatological  digestive  ...  glu_field  hba1c  \
0                   0.0             0.0        0.0  ...       5.02    5.2   
1                   0.0             0.0        0.0  ...       5.79    5.4   
2                   0.0             0.0        0.0  ...       4.98    5.0   
3                   0.0             0.0        0.0  ...       5.99    5.5   
4                   0.0             0.0        0.0  ...       5.02    5.5   
...                 ...             ...        ...  ...        ...    ...   
9543                0.0             0.0        0.0  ...       3.72    5.7   
9544                0.0             0.0        0.0  ...       4.47    5.3   
9545                0.0             0.0        0.0  ...       4.39    5.4   
9546                0.0             0.0        0.0  ...       4.36    5.6   
9547                0.0             0.0        0.0  ...       4.78    6.0   

        tp   alb  glucose    tg    tc   alt    trf  trf_r  
0     79.2  51.8    5.184  3.13  6.40  28.0  231.0  0.567  
1     75.6  45.4    5.301  1.24  5.65  10.0  248.0  0.879  
2     84.1  46.5    4.491  0.94  4.03  15.0  220.0  2.190  
3     79.8  48.6    5.994  3.16  5.27  11.0  266.0  1.360  
4     79.3  47.1    4.563  1.26  4.86   8.0  284.0  1.140  
...    ...   ...      ...   ...   ...   ...    ...    ...  
9543  77.0  49.2    4.300  3.36  4.22  47.0  376.0  1.410  
9544  85.3  50.0    4.800  1.28  4.52  16.0  290.0  1.510  
9545  80.6  48.0    4.640  0.45  3.28  24.0  281.0  1.570  
9546  68.1  46.0    4.810  1.47  4.09  27.0  308.0  1.970  
9547  76.4  51.1    5.040  0.84  3.29  20.0  349.0  1.700  

[9548 rows x 57 columns]

## Construct ML feature and traget train and test matricies:

In [47]:
fixedFactorIdxs = list(range(1,26))
fixedFactors = list(data.columns[fixedFactorIdxs])
lifeStyleFactorIdxs = list(range(26,31))
lifestyleFactors = list(data.columns[lifeStyleFactorIdxs])
responseVariableIdxs = list(range(31,57))
responseVariables = list(data.columns[responseVariableIdxs])
# responseVariableIdxs.pop(-10) # If we want to get rid of glu_field
fatRelatedIdxs = [responseVariables.index('apo_a'), 
                  responseVariables.index('lp_a'), 
                  responseVariables.index('hdl_c'),
                  responseVariables.index('ldl_c'),
                  responseVariables.index('apo_b'),
                  responseVariables.index('tg'),
                  responseVariables.index('tc')]
gluRelatedIdxs = [responseVariables.index('ins'),
                      responseVariables.index('hba1c'),
                      responseVariables.index('glucose')
                      ]
print(responseVariables)
X = data[fixedFactors + lifestyleFactors].to_numpy()
Y = data[responseVariables].to_numpy()
X_Train, X_Test, Y_Train, Y_Test, cv = hF.shuffleAndSplit(X, Y, test_size=.2, n_splits=5)


['urea', 'ua', 'apo_a', 'lp_a', 'hs_crp', 'cre', 'hdl_c', 'ldl_c', 'apo_b', 'mg', 'fet', 'ins', 'hgb', 'wbc', 'rbc', 'plt', 'glu_field', 'hba1c', 'tp', 'alb', 'glucose', 'tg', 'tc', 'alt', 'trf', 'trf_r']


## Define models to train:

In [52]:
models = dict(ols=linear_model.LinearRegression(),
              lasso=linear_model.Lasso(alpha=.5),
              ridge=linear_model.Ridge(alpha=.5),
              elastic=linear_model.ElasticNet(alpha=.5, l1_ratio=0.5),
              randomForest = ensemble.RandomForestRegressor(random_state=0, 
                                                           max_features = 'auto', 
                                                           min_samples_leaf = 10,
                                                           n_estimators = 200)
             )

## Cross Validataion
#### (Need to come back to this)

In [ ]:
### (Need to come back to this)
hF.showDataSplits(Y_Train, Y_Test, cv)

## Train model on z-scored response variables
#### (Skip for now)

In [ ]:
# Train a model to predict Z-scored reponse variables as well: 
Y_Train_Zscore = (Y_Train-np.mean(Y_Train,axis=0))/np.std(Y_Train,axis=0)
trainedModels_zscore = {}
for name, mdl in models.items(): 
    print('Training ' + str(name) + '...')
    trainedModels_zscore.update({name : mdl.fit(X_Train,Y_Train_Zscore)})
print('finished')

In [35]:
# The code below will help with visualizations
X = X_Train
Y = Y_Train_Zscore
def plotSubjectModelPrediction_zscore(modelName = 'ridge', subjectIdx = 1016):
    import matplotlib.pyplot as plt
    import matplotlib.patches as patches
    f, ax = plt.subplots(figsize=(15, 8))
    y_predict = trainedModels_zscore[modelName].predict(X[int(subjectIdx),:].reshape(1, -1))
    plt.scatter(range(0,26), Y[subjectIdx,:].T,color = 'b',label = 'actual')
    plt.scatter(range(0,26), y_predict.T,color = 'r',label = 'expected')
    plt.plot([0,26],[0, 0])
    plt.xticks(range(0,26))
    plt.xticks(rotation=90)
    plt.ylim([-3,3])
    plt.xlim([-1,26])
    ax.set_xticklabels(responseVariables, fontsize=14)
    handles, labels = ax.get_legend_handles_labels()
    ax.legend(handles, labels, bbox_to_anchor=(1.2, 1), loc='upper right')
    
    # highlight glucose and fat related factors
    for tmp in gluRelatedIdxs:
        start = (tmp - .5, -3)
        width = .8
        height = 6
        tmpPatch= patches.Rectangle(start,width,height,color='b',alpha=.2)
        ax.add_patch(tmpPatch)

    for tmp in fatRelatedIdxs:
        start = (tmp - .5, -3)
        width = .8
        height = 6
        tmpPatch= patches.Rectangle(start,width,height,color='r',alpha=.2)
        ax.add_patch(tmpPatch)
    plt.xlim([-1,26])
    plt.title("Patient's current blood test")
    plt.ylabel('Biomarker level (z-score)')
    plt.rcParams.update({'font.size': 22})
#     plt.savefig("Sally's current blood test")
    plt.show()
# plotSubjectModelPrediction_zscore()

In [ ]:
# Show predictions interactively on the training dataset:
%matplotlib inline
from ipywidgets import FloatSlider, interactive, IntSlider, Dropdown
subjectSlider = IntSlider(value=998, min=0, max=7635, step=1)
modelSelector = Dropdown(
    options=list(models.keys()),
    value='randomForest',
    description='Model:',
    disabled=False,
)
interactive(
    plotSubjectModelPrediction_zscore,
    subjectIdx=subjectSlider,
    modelName = modelSelector
    )    

## Train models

In [53]:
# Train model
trainedModels = {}
for name, mdl in models.items(): 
    print('Training ' + str(name) + '...')
    trainedModels.update({name : mdl.fit(X_Train,Y_Train)})
print('finished')

Training ols...
Training lasso...
Training ridge...
Training elastic...
Training randomForest...
finished


## Define functions for viz

In [54]:
inputFeatures = fixedFactors+lifestyleFactors
inputFeatures
def getCurrEstimate(modelName = 'randomForest', age = 25, sex = 'M',
                       location = 'urban', medicalCondition = 'noReport',
                       currCarbo = 289, currFat = 73, currProtn = 65,
                       currActivityLevel = 1):
    inputValues=np.zeros(len(inputFeatures))
    # Age
    inputValues[inputFeatures.index('age')] = age

    # Sex
    if sex == 'M':
        inputValues[inputFeatures.index('sex')] = 1
    else: 
        inputValues[inputFeatures.index('sex')] = 0

    # Location:
    if location == 'urban':
        inputValues[inputFeatures.index('urban')] = 1
    else: 
        inputValues[inputFeatures.index('urban')] = 0

    # Medical Condition: 
    inputValues[inputFeatures.index(medicalCondition)] = 1

    ### Current lifestyle
    # Diet
    inputValues[inputFeatures.index('kcal')] = currCarbo*4 + currProtn*4 + currFat*9 #currKcal
    inputValues[inputFeatures.index('carbo')] = currCarbo
    inputValues[inputFeatures.index('fat')] = currFat
    inputValues[inputFeatures.index('protn')] = currProtn
    inputValues[inputFeatures.index('activityLevel')] = currActivityLevel

    currEstimate = trainedModels[modelName].predict(inputValues.reshape(1, -1))
#     print(inputValues.reshape(1, -1))
    return currEstimate

def getIntEstimate(modelName = 'randomForest', age = 25, sex = 'M',
                       location = 'urban', medicalCondition = 'noReport',
                       intCarbo = 289, intFat = 73, intProtn = 65,
                       intActivityLevel = 5):
    inputValues=np.zeros(len(inputFeatures))
    # Age
    inputValues[inputFeatures.index('age')] = age

    # Sex
    if sex == 'M':
        inputValues[inputFeatures.index('sex')] = 1
    else: 
        inputValues[inputFeatures.index('sex')] = 0

    # Location:
    if location == 'urban':
        inputValues[inputFeatures.index('urban')] = 1
    else: 
        inputValues[inputFeatures.index('urban')] = 0

    # Medical Condition: 
    inputValues[inputFeatures.index(medicalCondition)] = 1

    ### Current lifestyle
    # Diet
    inputValues[inputFeatures.index('kcal')] = intCarbo*4 + intProtn*4 + intFat*9 #intKcal
    inputValues[inputFeatures.index('carbo')] = intCarbo
    inputValues[inputFeatures.index('fat')] = intFat
    inputValues[inputFeatures.index('protn')] = intProtn
    inputValues[inputFeatures.index('activityLevel')] = intActivityLevel

    intEstimate = trainedModels[modelName].predict(inputValues.reshape(1, -1))
#     print(inputValues.reshape(1, -1))
    return intEstimate

def calcExpectedChange(modelName = 'ols', age = 25, sex = 'M',
                       location = 'urban', medicalCondition = 'noReport',
                       currCarbo = 289, currFat = 73, currProtn = 65,
                       currActivityLevel = 1, 
                       intCarbo = 289, intFat = 73, intProtn = 65,
                       intActivityLevel = 1): 
    
    currEstimate = getCurrEstimate(modelName = modelName, age = age, sex = sex,
                       location = location, medicalCondition = medicalCondition, 
                       currCarbo = currCarbo, currFat = currFat, currProtn = currProtn,
                       currActivityLevel = currActivityLevel)
    
    intEstimate = getIntEstimate(modelName = modelName, age = age, sex = sex,
                       location = location, medicalCondition = medicalCondition,
                       intCarbo = intCarbo, intFat = intFat, intProtn = intProtn,
                       intActivityLevel = intActivityLevel)
    
    expectedChange = intEstimate/currEstimate-1
    return expectedChange
calcExpectedChange()

def plotExpectedChange(modelName = 'randomForest', age = 25, sex = 'M',
                       location = 'urban', medicalCondition = 'noReport',
                       currCarbo = 289, currFat = 73, currProtn = 65,
                       currActivityLevel = 1, 
                       intCarbo = 289, intFat = 73, intProtn = 65,
                       intActivityLevel = 1):
    
    expectedChange = calcExpectedChange(modelName = modelName, age = age, sex = sex,
                       location = location, medicalCondition = medicalCondition,
                       currCarbo = currCarbo, currFat = currFat, currProtn = currProtn, 
                       currActivityLevel = currActivityLevel, 
                       intCarbo = intCarbo, intFat = intFat, intProtn = intProtn,
                       intActivityLevel = intActivityLevel)
    import matplotlib as mpl
    import matplotlib.pyplot as plt
    import matplotlib.patches as patches
    f, ax = plt.subplots(figsize=(15, 7))
    plt.scatter(range(0,26), expectedChange*100,color = 'r',label = 'predicted change')
    plt.plot([0,26],[0, 0])
    plt.xticks(range(0,26))
    plt.xticks(rotation=90)
    plt.ylim([-100,100])
    plt.xlim([-1,26])
    ax.set_xticklabels(responseVariables, fontsize = 14)
    handles, labels = ax.get_legend_handles_labels()
    ax.legend(handles, labels, bbox_to_anchor=(1.35, 1), loc='upper right')

    # highlight glucose and fat related factors
    for idx in gluRelatedIdxs:
        start = (idx - .5, -100)
        width = .8
        height = 200
        tmpPatch= patches.Rectangle(start,width,height,color='b',alpha=.2)
        ax.add_patch(tmpPatch)
        ax.text(idx-.5, -90, '{:.2f}'.format(expectedChange[0][idx]))


    for idx in fatRelatedIdxs:
        start = (idx - .5, -100)
        width = .8
        height = 200
        tmpPatch= patches.Rectangle(start,width,height,color='r',alpha=.2)
        ax.add_patch(tmpPatch)
#         ax.text(idx-.5, -.9, '{:.2f}'.format(expectedChange[0][idx]))
    
    plt.xlim([-1,26])
    plt.title('Predicted change in blood tests')
    plt.ylabel('% change in biomarker')
    plt.rcParams.update({'font.size': 22})
    plt.show()


#  Insight demo week 2

In [62]:
# Create interactive predictions: 
from ipywidgets import FloatSlider, interactive, IntSlider, Dropdown
sexs = ['F','M']
locations = ['rural','urban']
medicalConditions = ['ENT',
                     'OBGYN',
                     'Old_age_midLife_syndrome',
                     'alcohol_poisoning',
                     'dermatological',
                     'digestive',
                     'endocrine',
                     'heart',
                     'hematological',
                     'infectious_parasitic',
                     'injury',
                     'muscular_rheumatological',
                     'neurological',
                     'noDiagnosis',
                     'noReport',
                     'other',
                     'pyschiatric',
                     'respiratory',
                     'sexualDysfunction',
                     'tumor',
                     'unknown',
                     'urinary']
# UIs:
modelSelector = Dropdown(
    options=list(models.keys()),
    value='randomForest',
    description='Model:',
    disabled=False,
)
ageSlider = IntSlider(65, min=0, max=100, step=1)
sexSelector = Dropdown(options=sexs,
                       value='F',
                       description='Sex:',
                       disabled=False)

locationSelector = Dropdown(options=locations,
                        value='rural',
                        description='Location:',
                        disabled=False)

medicalConditionSelector = Dropdown(options=medicalConditions,
                                    value='noReport',
                                    description='Medical Conditions:',
                                    disabled=False)

# currKcalSlider = IntSlider(value=data['kcal'].mean(), min=0, max=5000, step=50)
currCarboSlider = IntSlider(600, min=0, max=600, step=20)
currFatSlider = IntSlider(120, min=0, max=120, step=5)
currProtnSlider = IntSlider(value=data['protn'].mean(), min=0, max=150, step=5)
currActivityLevelSlider = IntSlider(value=data['activityLevel'].mean(), min=1, max=5, step=1)
intCarboSlider = IntSlider(600, min=0, max=600, step=20)
intFatSlider = IntSlider(120, min=0, max=120, step=5)
intProtnSlider = IntSlider(value=data['protn'].mean(), min=0, max=150, step=5)
intActivityLevelSlider = IntSlider(value=data['activityLevel'].mean(), min=1, max=5, step=1)

interactive(plotExpectedChange,
    modelName = modelSelector,
    age = ageSlider,
    sex = sexSelector,
    location = locationSelector,
    medicalCondition = medicalConditionSelector,
    currCarbo = currCarboSlider, 
    currFat = currFatSlider, 
    currProtn = currProtnSlider,
    currActivityLevel = currActivityLevelSlider,
    intCarbo = intCarboSlider,
    intFat = intFatSlider,
    intProtn = intProtnSlider,
    intActivityLevel = intActivityLevelSlider)

interactive(children=(Dropdown(description='Model:', index=4, options=('ols', 'lasso', 'ridge', 'elastic', 'ra…

RandomForestRegressor(bootstrap=True, criterion='mse', max_depth=None,
                      max_features='auto', max_leaf_nodes=None,
                      min_impurity_decrease=0.0, min_impurity_split=None,
                      min_samples_leaf=10, min_samples_split=2,
                      min_weight_fraction_leaf=0.0, n_estimators=200,
                      n_jobs=None, oob_score=False, random_state=0, verbose=0,
                      warm_start=False)

In [ ]:
# Create interactive predictions: 
from ipywidgets import FloatSlider, interactive, IntSlider, Dropdown
sexs = ['F','M']
locations = ['rural','urban']
medicalConditions = ['ENT',
                     'OBGYN',
                     'Old_age_midLife_syndrome',
                     'alcohol_poisoning',
                     'dermatological',
                     'digestive',
                     'endocrine',
                     'heart',
                     'hematological',
                     'infectious_parasitic',
                     'injury',
                     'muscular_rheumatological',
                     'neurological',
                     'noDiagnosis',
                     'noReport',
                     'other',
                     'pyschiatric',
                     'respiratory',
                     'sexualDysfunction',
                     'tumor',
                     'unknown',
                     'urinary']
# UIs:
modelSelector = Dropdown(
    options=list(models.keys()),
    value='randomForest',
    description='Model:',
    disabled=False,
)
ageSlider = IntSlider(value=data['age'].mean(), min=0, max=100, step=1)
sexSelector = Dropdown(options=sexs,
                       value='M',
                       description='Sex:',
                       disabled=False)

locationSelector = Dropdown(options=locations,
                        value='rural',
                        description='Location:',
                        disabled=False)

medicalConditionSelector = Dropdown(options=medicalConditions,
                                    value='noReport',
                                    description='Medical Conditions:',
                                    disabled=False)

# currKcalSlider = IntSlider(value=data['kcal'].mean(), min=0, max=5000, step=50)
currCarboSlider = IntSlider(value=data['carbo'].mean(), min=0, max=600, step=20)
currFatSlider = IntSlider(value=data['fat'].mean(), min=0, max=120, step=5)
currProtnSlider = IntSlider(value=data['protn'].mean(), min=0, max=150, step=5)
currActivityLevelSlider = IntSlider(value=data['activityLevel'].mean(), min=1, max=5, step=1)
intCarboSlider = IntSlider(value=data['carbo'].mean(), min=0, max=600, step=20)
intFatSlider = IntSlider(value=data['fat'].mean(), min=0, max=120, step=5)
intProtnSlider = IntSlider(value=data['protn'].mean(), min=0, max=150, step=5)
intActivityLevelSlider = IntSlider(value=data['activityLevel'].mean(), min=1, max=5, step=1)

interactive(plotExpectedChange,
    modelName = modelSelector,
    age = ageSlider,
    sex = sexSelector,
    location = locationSelector,
    medicalCondition = medicalConditionSelector,
    currCarbo = currCarboSlider, 
    currFat = currFatSlider, 
    currProtn = currProtnSlider,
    currActivityLevel = currActivityLevelSlider,
    intCarbo = intCarboSlider,
    intFat = intFatSlider,
    intProtn = intProtnSlider,
    intActivityLevel = intActivityLevelSlider)
    